# Business Data Challenge - Team 1

In [1]:
import pandas as pd
import numpy as np
import os
import s3fs
import re

Configuration de l'accès aux données

In [2]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})

# Exemple sur Company 1

## Chargement données

In [3]:
BUCKET = "bdc2324-data/1"
liste_database = fs.ls(BUCKET)

In [4]:
liste_database

['bdc2324-data/1/1campaign_stats.csv',
 'bdc2324-data/1/1campaigns.csv',
 'bdc2324-data/1/1categories.csv',
 'bdc2324-data/1/1countries.csv',
 'bdc2324-data/1/1currencies.csv',
 'bdc2324-data/1/1customer_target_mappings.csv',
 'bdc2324-data/1/1customersplus.csv',
 'bdc2324-data/1/1event_types.csv',
 'bdc2324-data/1/1events.csv',
 'bdc2324-data/1/1facilities.csv',
 'bdc2324-data/1/1link_stats.csv',
 'bdc2324-data/1/1pricing_formulas.csv',
 'bdc2324-data/1/1product_packs.csv',
 'bdc2324-data/1/1products.csv',
 'bdc2324-data/1/1products_groups.csv',
 'bdc2324-data/1/1purchases.csv',
 'bdc2324-data/1/1representation_category_capacities.csv',
 'bdc2324-data/1/1representations.csv',
 'bdc2324-data/1/1seasons.csv',
 'bdc2324-data/1/1structure_tag_mappings.csv',
 'bdc2324-data/1/1suppliers.csv',
 'bdc2324-data/1/1tags.csv',
 'bdc2324-data/1/1target_types.csv',
 'bdc2324-data/1/1targets.csv',
 'bdc2324-data/1/1tickets.csv',
 'bdc2324-data/1/1type_of_categories.csv',
 'bdc2324-data/1/1type_of_pr

In [5]:
# loop to create dataframes from liste
files_path = liste_database

client_number = files_path[0].split("/")[1]
df_prefix = "df" + str(client_number) + "_"

for i in range(len(files_path)) :
    current_path = files_path[i]
    with fs.open(current_path, mode="rb") as file_in:
        df = pd.read_csv(file_in)
        # the pattern of the name is df1xxx
        nom_dataframe = df_prefix + re.search(r'\/(\d+)\/(\d+)([a-zA-Z_]+)\.csv$', current_path).group(3)
        globals()[nom_dataframe] = df

/tmp/ipykernel_50143/4081512283.py:10: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_in)


## Cleaning functions

In [6]:
def cleaning_date(df, column_name):
    """
    Nettoie la colonne spécifiée du DataFrame en convertissant les valeurs en datetime avec le format ISO8601.

    Parameters:
    - df: DataFrame
        Le DataFrame contenant la colonne à nettoyer.
    - column_name: str
        Le nom de la colonne à nettoyer.

    Returns:
    - DataFrame
        Le DataFrame modifié avec la colonne nettoyée.
    """
    df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
    return df

## Preprocessing

## customer_plus

## Ticket area

In [7]:
# Fonction de nettoyage et selection
def preprocessing_tickets_area(tickets = None, purchases = None, suppliers = None, type_ofs = None):
    # Base des tickets
    tickets = tickets[['id', 'purchase_id', 'product_id', 'is_from_subscription', 'type_of', 'supplier_id']]
    tickets.rename(columns = {'id' : 'ticket_id'}, inplace = True)

    # Base des fournisseurs
    suppliers = suppliers[['id', 'name']]
    suppliers.rename(columns = {'name' : 'supplier_name'}, inplace = True)

    # Base des types de billets
    # type_ofs = type_ofs[['id', 'name', 'children']]
    # type_ofs.rename(columns = {'name' : 'type_of_ticket_name'}, inplace = True)

    # Base des achats
    # Nettoyage de la date d'achat
    cleaning_date(purchases, 'purchase_date')
    # Selection des variables
    purchases = purchases[['id', 'purchase_date', 'customer_id']]

    # Fusions 
    # Fusion avec fournisseurs
    ticket_information = pd.merge(tickets, suppliers, left_on = 'supplier_id', right_on = 'id', how = 'inner')
    ticket_information.drop(['supplier_id', 'id'], axis = 1, inplace=True)
    
    # # Fusion avec type de tickets
    # ticket_information = pd.merge(ticket_information, type_ofs, left_on = 'type_of', right_on = 'id', how = 'inner')
    # ticket_information.drop(['type_of', 'id'], axis = 1, inplace=True)
    
    # Fusion avec achats
    ticket_information = pd.merge(ticket_information, purchases, left_on = 'purchase_id', right_on = 'id', how = 'inner')
    ticket_information.drop(['purchase_id', 'id'], axis = 1, inplace=True)

    return ticket_information

In [8]:
df1_ticket_information = preprocessing_tickets_area(tickets = df1_tickets, purchases = df1_purchases, suppliers = df1_suppliers, type_ofs = df1_type_ofs)

/tmp/ipykernel_50143/1320335767.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tickets.rename(columns = {'id' : 'ticket_id'}, inplace = True)
/tmp/ipykernel_50143/1320335767.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  suppliers.rename(columns = {'name' : 'supplier_name'}, inplace = True)


In [70]:
df1_ticket_information

ticket_id  product_id  is_from_subscription  type_of   supplier_name  \
0         13070859      225251                 False        1  vente en ligne   
1         13070860      224914                 False        1  vente en ligne   
2         13070861      224914                 False        1  vente en ligne   
3         13070862      224914                 False        1  vente en ligne   
4         13070863      224914                 False        1  vente en ligne   
...            ...         ...                   ...      ...             ...   
1826667   20662815      405689                 False        1  vente en ligne   
1826668   20662816      403658                 False        1  vente en ligne   
1826669   20662817      403658                 False        1  vente en ligne   
1826670   20662818      403658                 False        1  vente en ligne   
1826671   20662819      403658                 False        1  vente en ligne   

                    purchase_date  customer_id  
0       2018-12-28 14:47:50+00:00        48187  
1       2018-12-28 14:47:50+00:00        48187  
2       2018-12-28 14:47:50+00:00        48187  
3       2018-12-28 14:47:50+00:00        48187  
4       2018-12-28 14:47:50+00:00        48187  
...                           ...          ...  
1826667 2023-11-08 17:23:54+00:00      1256135  
1826668 2023-11-08 18:32:18+00:00      1256136  
1826669 2023-11-08 18:32:18+00:00      1256136  
1826670 2023-11-08 19:30:28+00:00      1256137  
1826671 2023-11-08 19:30:28+00:00      1256137  

[1826672 rows x 7 columns]

## Target area

In [9]:
def preprocessing_target_area(targets = None, target_types = None, customer_target_mappings = None):
    # Target.csv cleaning
    targets = targets[["id", "target_type_id", "name"]]
    targets.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)
    
    # target_type cleaning
    target_types = target_types[["id","is_import","name"]].add_prefix("target_type_")
    
    #customer_target_mappings cleaning
    customer_target_mappings = customer_target_mappings[["id", "customer_id", "target_id"]]
    
    # Merge target et target_type
    targets_full = pd.merge(targets, target_types, left_on='target_type_id', right_on='target_type_id', how='inner')
    targets_full.drop(['target_type_id'], axis = 1, inplace=True)
    
    # Merge
    targets_full = pd.merge(customer_target_mappings, targets_full, left_on='target_id', right_on='target_id', how='inner')
    targets_full.drop(['target_id'], axis = 1, inplace=True)

    return targets_full

In [10]:
df1_target_information = preprocessing_target_area(targets = df1_targets, target_types = df1_target_types, customer_target_mappings = df1_customer_target_mappings)

/tmp/ipykernel_50143/3848597476.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  targets.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)


In [19]:
df1_target_information[['target_name', 'customer_id']].groupby('target_name').count().sort_values(by='customer_id', ascending=False)

customer_id
target_name                                                  
consentement optin mediation specialisee               150000
consentement optin jeune public                        149979
consentement optin b2c                                 108909
Arenametrix_bascule tel vers sib                        35216
consentement optout b2c                                 34523
...                                                       ...
Automation_parrainage_newsletter_handicap_visuel            1
consentement optout mediation specialisee                   1
Inscrits NL LSF formulaire                                  1
Market auto - contacts inactifs post-scénario               1
Inactifs - fin du scénario                                  1

[283 rows x 1 columns]

In [29]:
df1_target_information_reduced = df1_target_information[['target_name', 'customer_id']].groupby('target_name').count()
df1_target_information_reduced[df1_target_information_reduced['customer_id'] >= 1000]

customer_id
target_name                                                    
Arenametrix_bascule tel vers sib                          35216
Autres_interet_exposition                                  1021
COM Inscrits NL générale (historique)                     23005
Contacts_prenomsdoubles                                   11643
DDCP MD Procès du Siècle                                   1684
DDCP Newsletter centres de loisirs                         1032
DDCP Newsletter enseignants                                4510
DDCP Newsletter jeune public                               3862
DDCP Newsletter relais champ social                        2270
DDCP PROMO Participants ateliers (adultes et en...         1954
DDCP billets famille                                       3609
DDCP promo MD pass musées dps oct 2018                     1785
DDCP promo Plan B 2019 (concerts)                          1948
DDCP promo spectateurs prog 21-22 (spectacles, ...         1293
DDCP rentrée culturelle 2023                               1757
DDCP_marseille_jazz_2023                                   1043
DRE Festival Jean Rouch                                    1502
DRE MucemLab                                               2302
DRE chercheurs                                             1557
DRE institutionnels                                        2229
FORMATION _ acheteurs optin last year                     10485
Inscrits NL générale (export_291019 + operation...        14086
Inscrits NL générale site web                              3732
Inscrits NL jeune public site web                          1249
Votre première liste                                       3715
consentement optin b2b                                    12735
consentement optin b2c                                   108909
consentement optin dre                                     4527
consentement optin jeune public                          149979
consentement optin mediation specialisee                 150000
consentement optin newsletter generale                    22095
consentement optin scolaires                               4849
consentement optout b2b                                   14219
consentement optout b2c                                   34523
consentement optout dre                                   14328
consentement optout newsletter generale                   18855
consentement optout scolaires                             15744
ddcp_md_scene_ouverte_au_talent                            1577
ddcp_promo_MD_billet_musée_oct_2019_agarder2               5482
ddcp_promo_md_musée_dps 011019                             6010
ddcp_promo_visiteurs occasionnels_musee_8mois              6640
ddcp_visiteurs dps 010622                                 12355
festival_jean_rouch                                        1502
rappel po barvalo                                          1248
structures_etiquette champ social                          1488

## Campaings area

In [11]:
def preprocessing_campaigns_area(campaign_stats = None, campaigns = None):
    # campaign_stats cleaning 
    campaign_stats = campaign_stats[["id", "campaign_id", "customer_id", "opened_at", "sent_at", "delivered_at"]]
    cleaning_date(campaign_stats, 'opened_at')
    cleaning_date(campaign_stats, 'sent_at')
    cleaning_date(campaign_stats, 'delivered_at')
    
    # campaigns cleaning
    campaigns = campaigns[["id", "name", "service_id", "sent_at"]].add_prefix("campaign_")
    cleaning_date(campaigns, 'campaign_sent_at')
    
    # Merge 
    campaigns_full = pd.merge(campaign_stats, campaigns, on = "campaign_id", how = "left")
    campaigns_full.drop(['campaign_id'], axis = 1, inplace=True)

    return campaigns_full

In [12]:
df1_campaigns_information = preprocessing_campaigns_area(campaign_stats = df1_campaign_stats, campaigns = df1_campaigns)

/tmp/ipykernel_50143/1967867975.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
/tmp/ipykernel_50143/1967867975.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
/tmp/ipykernel_50143/1967867975.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

In [27]:
df1_campaigns_information

id  customer_id                 opened_at  \
0          19793       112597                       NaT   
1          14211       113666                       NaT   
2          13150       280561                       NaT   
3           7073       101007 2021-03-28 18:11:06+00:00   
4           5175       103972                       NaT   
...          ...          ...                       ...   
6214803  8302994       266155 2023-10-23 09:43:25+00:00   
6214804  8303307        21355 2023-10-23 09:44:02+00:00   
6214805  8304346        21849 2023-10-23 09:45:52+00:00   
6214806  8302037       667789 2023-10-23 09:47:32+00:00   
6214807  8304939       294154                       NaT   

                          sent_at              delivered_at  \
0       2021-03-28 16:01:09+00:00 2021-03-28 16:24:18+00:00   
1       2021-03-28 16:01:09+00:00 2021-03-28 16:21:02+00:00   
2       2021-03-28 16:00:59+00:00 2021-03-28 16:08:45+00:00   
3       2021-03-28 16:00:59+00:00 2021-03-28 16:09:47+00:00   
4       2021-03-28 16:01:06+00:00 2021-03-28 16:05:03+00:00   
...                           ...                       ...   
6214803 2023-10-23 09:32:33+00:00 2023-10-23 09:32:34+00:00   
6214804 2023-10-23 09:32:49+00:00 2023-10-23 09:32:49+00:00   
6214805 2023-10-23 09:33:28+00:00 2023-10-23 09:33:29+00:00   
6214806 2023-10-23 09:31:53+00:00 2023-10-23 09:31:54+00:00   
6214807 2023-10-23 09:33:54+00:00 2023-10-23 09:33:55+00:00   

                                   campaign_name  campaign_service_id  \
0        Le Mucem chez vous, gardons le lien #22                  404   
1        Le Mucem chez vous, gardons le lien #22                  404   
2        Le Mucem chez vous, gardons le lien #22                  404   
3        Le Mucem chez vous, gardons le lien #22                  404   
4        Le Mucem chez vous, gardons le lien #22                  404   
...                                          ...                  ...   
6214803                             dre_nov_2023                 1318   
6214804                             dre_nov_2023                 1318   
6214805                             dre_nov_2023                 1318   
6214806                             dre_nov_2023                 1318   
6214807                             dre_nov_2023                 1318   

                 campaign_sent_at  
0       2021-03-27 23:00:00+00:00  
1       2021-03-27 23:00:00+00:00  
2       2021-03-27 23:00:00+00:00  
3       2021-03-27 23:00:00+00:00  
4       2021-03-27 23:00:00+00:00  
...                           ...  
6214803 2023-10-23 09:31:17+00:00  
6214804 2023-10-23 09:31:17+00:00  
6214805 2023-10-23 09:31:17+00:00  
6214806 2023-10-23 09:31:17+00:00  
6214807 2023-10-23 09:31:17+00:00  

[6214808 rows x 8 columns]

In [67]:
def campaigns_kpi(campaigns_information = None):
    # Nombre de campagnes de mails
    nb_campaigns = campaigns_information[['customer_id', 'campaign_name']].groupby('customer_id').count().reset_index()
    nb_campaigns.rename(columns = {'campaign_name' : 'nb_campaigns'}, inplace = True)
    # Temps d'ouverture en min moyen    
    campaigns_information['time_to_open'] = campaigns_information['opened_at'] - campaigns_information['delivered_at']
    time_to_open = campaigns_information[['customer_id', 'time_to_open']].groupby('customer_id').mean().reset_index()

    # Nombre de mail ouvert    
    opened_campaign = campaigns_information[['customer_id', 'campaign_name', 'opened_at']]
    opened_campaign.dropna(subset=['opened_at'], inplace=True)
    opened_campaign = opened_campaign[['customer_id', 'campaign_name']].groupby('customer_id').count().reset_index()
    opened_campaign.rename(columns = {'campaign_name' : 'nb_campaigns_opened' }, inplace = True)

    # Fusion des indicateurs
    campaigns_reduced = pd.merge(nb_campaigns, opened_campaign, on = 'customer_id', how = 'left')
    campaigns_reduced = pd.merge(campaigns_reduced, time_to_open, on = 'customer_id', how = 'left')

    # Remplir les NaN : nb_campaigns_opened
    campaigns_reduced['nb_campaigns_opened'].fillna(0, inplace=True)

    # Remplir les NaT : time_to_open (??)

    return campaigns_reduced
    

In [69]:
df1_campaigns_kpi = campaigns_kpi(campaigns_information = df1_campaigns_information) 

/tmp/ipykernel_50143/2679359833.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opened_campaign.dropna(subset=['opened_at'], inplace=True)
/tmp/ipykernel_50143/2679359833.py:20: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  campaigns_reduced['nb_campaigns_opened'].fillna(0, inplace=True)


In [66]:
df1_campaigns_kpi

customer_id  nb_campaigns  nb_campaigns_opened  \
0                 2             4                  0.0   
1                 3           222                124.0   
2                 4             7                  7.0   
3                 5             4                  0.0   
4                 6            20                  0.0   
...             ...           ...                  ...   
130467      1256097             1                  1.0   
130468      1256098             1                  0.0   
130469      1256099             1                  0.0   
130470      1256100             1                  0.0   
130471      1256101             1                  0.0   

                    time_to_open  
0                            NaT  
1      1 days 00:28:30.169354838  
2      1 days 04:31:01.428571428  
3                            NaT  
4                            NaT  
...                          ...  
130467           0 days 02:11:15  
130468                       NaT  
130469                       NaT  
130470                       NaT  
130471                       NaT  

[130472 rows x 4 columns]